<p float="left">
  <img src="PlantHub-full-rgb.png" style="height:100px" alt="PlantHub logo" class="light-logo">
  <img src="PlantHub-full-white.png" style="height:100px" alt="PlantHub logo" class="dark-logo">
  <img src="gfoe.png" style="height:100px" alt="gfö logo" class="light-logo">
  <img src="gfoe_inv.png" style="height:100px" alt="gfö logo" class="dark-logo">
  <img src="NFDI4Biodiversity.svg" style="height:100px" alt="NFDI logo" class="light-logo">
   <img src="NFDI4Biodiversity_text_inv.svg" style="height:100px" alt="NFDI 2023 logo" class="dark-logo">
</p>

# Taxonomic name resolution

This notebook is intended to demonstrate the workflow of taxonomic name resolution. Taxonomic name resolution is the process of checking and de-synonymizing taxonomic names using a reference database. This is necessary because many taxonomic entities, such as species, are known and have been described using several scientific names. However, only one of those scientific names is the <b>accepted name</b>, while the others are referred to as <b>synonyms</b> (although there are special cases, e.g., unresolved names). To correctly link data from several sources, it is necessary to check and de-synonymize names using a common reference database.

This process is complicated by spelling errors, names not found in the database, and other challenges. In this notebook, we will utilize the powerful [GBIF API](https://techdocs.gbif.org/en/openapi/) to resolve the names from a sample list. However, users may not always want to apply the GBIF taxonomy, and not all datasets incorporated in GBIF are the newest versions. Therefore, in the hands on-part of this notebook, we will attempt to create a custom name resolution function using the [Leipzig Catalogue of Vascular Plants (LCVP)](https://planthub.idiv.de/LCVP/). We will also strive to speed up the name resolution process by using the parallel processing functionality of R.

## Prerequisites

To run the code presented here, you will need 
- the sample names list provided in the workshop,
- a version of the Leipzig Catalogue of Vascular Plants (LCVP), also provided in the workshop,
- a functioning R environment and 
- the R packages `data.table`, `rgbif`, and `doSNOW` installed.

## Code

The first block of code loads libraries and prepares the workspace. You will need to adapt the working directory.

In [1]:
# load packages
library(data.table) # handle large datasets
library(rgbif) # access GBIF data
library(doSNOW) # parallel computing

# clear workspace
rm(list = ls())

# set working directory
setwd(paste0(.brd, "gfoe NFDI taxonomic harmonization workshop"))

# load data
plants <- fread("plant names_2024-04-08.txt", sep = "\t")
animals <- fread("animal names_2024-04-09.txt", sep = "\t")


Lade nötiges Paket: foreach

Lade nötiges Paket: iterators

Lade nötiges Paket: snow



For the sake of simplicity, we will proceed to do the name matching using the names as they are. Note that name parsing can help to increase the accuracy and efficiency of the name harmonization process.

### Encoding

Unfortunately, when getting data from differing sources, we will often find that these data have been [encoded](https://en.wikipedia.org/wiki/Binary-to-text_encoding) in different ways. This means that while the typical English language letters will be stored the same way on any machine, when it comes to accents and some other special characters, it may matter whether data was stored by a computer in the US or Japan, and whether the computer has a Windows, Mac, or Linux operating system. 

We will deal with the most common case: Data being stored in the Windows-specific [CP-1252 encoding](https://en.wikipedia.org/wiki/Windows-1252) (mislabeled ANSI or latin1 sometimes) and not in [UTF-8](https://en.wikipedia.org/wiki/UTF-8).

How your machine treats data from different encodings depends on what encoding is preset in your console. You can check this using the following:

In [2]:
Sys.getlocale()


[1] "LC_COLLATE=German_Germany.utf8;LC_CTYPE=German_Germany.utf8;LC_MONETARY=German_Germany.utf8;LC_NUMERIC=C;LC_TIME=German_Germany.utf8"

If your console has no UTF-8 setting (no matter the language) you may change it like this: 

`Sys.setlocale(category = "LC_ALL", locale = "German_Germany.utf8")`

You can use another encoding, too, but it may throw errors later on. So let's check whether the data comes in UTF-8, and if not, let's repair it, assuming it is CP-1252 (our best guess, likely correct in 99% of the cases).

In [3]:
# check whether correct encoding is UTF-8
table(validUTF8(plants$oldName))
table(validUTF8(animals$modName))



FALSE  TRUE 
   73  4927 


TRUE 
5000 

In [4]:
# create new columns for variables
plants[, newName := oldName]
animals[, newName := modName]
# correct encoding, assuming current encoding is CP-1252
plants[!validUTF8(newName), newName := iconv(newName, from = "CP1252", to = "UTF-8")]


### Name resolution

To access the GBIF backbone, we can use the `name_backbone_checklist` function found in the rgbif package.

In [5]:
resP <- data.table(name_backbone_checklist(plants$newName))
resA <- data.table(name_backbone_checklist(animals$newName))


It took some time, but we got some results. Let's look at the result structure.

In [6]:
str(resP)


Classes 'data.table' and 'data.frame':	5000 obs. of  25 variables:
 $ confidence      : int  100 100 100 98 94 98 94 99 99 99 ...
 $ matchType       : chr  "NONE" "NONE" "NONE" "EXACT" ...
 $ synonym         : logi  FALSE FALSE FALSE TRUE FALSE TRUE ...
 $ usageKey        : int  NA NA NA 2977925 3152705 2685510 2684876 8132859 3138531 3830289 ...
 $ acceptedUsageKey: int  NA NA NA 11698476 NA 2685508 NA NA NA NA ...
 $ scientificName  : chr  NA NA NA "Abarema curvicarpa (H.S.Irwin) Barneby & J.W.Grimes" ...
 $ canonicalName   : chr  NA NA NA "Abarema curvicarpa" ...
 $ rank            : chr  NA NA NA "SPECIES" ...
 $ status          : chr  NA NA NA "SYNONYM" ...
 $ kingdom         : chr  NA NA NA "Plantae" ...
 $ phylum          : chr  NA NA NA "Tracheophyta" ...
 $ order           : chr  NA NA NA "Fabales" ...
 $ family          : chr  NA NA NA "Fabaceae" ...
 $ genus           : chr  NA NA NA "Jupunba" ...
 $ species         : chr  NA NA NA "Jupunba curvicarpa" ...
 $ kingdomKey     

As there is a column named "kingdom", we might check whether we actually got all plants matched, and how many non-matches we got. Another important information can be found in the "matchType" column. Here, we can see whether names were retrieved exactly as they wer spelled, or some fuzzy matching was done, or whether they could only be matched to a higher rank. The latter means that names may only have been matched to genus, familiy, order, or phylum level. It is worth checking these results.

In [7]:
table(resP$kingdom)
sum(is.na(resP$kingdom))
table(resP$matchType)



Animalia    Fungi  Plantae 
       1       40     4814 

[1] 145


     EXACT      FUZZY HIGHERRANK       NONE 
      4550        138        167        145 

In [8]:
resP[kingdom != "Plantae"]


confidence matchType synonym usageKey acceptedUsageKey
1  99         EXACT     FALSE    3414350       NA        
2  99         EXACT     FALSE    2592767       NA        
3  99         EXACT     FALSE    7250670       NA        
4  99         EXACT     FALSE    3419869       NA        
5  98         EXACT      TRUE    2608288  3438532        
6  99         EXACT     FALSE    2609464       NA        
7  99         EXACT     FALSE    2609287       NA        
8  98         EXACT      TRUE    2610162  7462577        
9  98         EXACT      TRUE    3469366  2596842        
10 99         EXACT     FALSE    7186902       NA        
11 99         EXACT     FALSE    3391187       NA        
12 99         EXACT     FALSE    2607718       NA        
13 97         EXACT     FALSE   10883702       NA        
14 99         EXACT     FALSE    3433571       NA        
15 97         EXACT     FALSE    5475464       NA        
16 98         EXACT      TRUE    2606991  2606897        
17 99         EXACT     FALSE    3439134       NA        
18 99         EXACT     FALSE    2600912       NA        
19 99         EXACT     FALSE    2601899       NA        
20 98         EXACT      TRUE    5517083 10809472        
21 99         EXACT     FALSE    3424580       NA        
22 98         EXACT      TRUE    2605920  2605922        
23 97         EXACT     FALSE    2601157       NA        
24 99         EXACT     FALSE    2600005       NA        
25 98         EXACT      TRUE    8460032  3291408        
26 99         EXACT     FALSE    3477254       NA        
27 99         EXACT     FALSE    7251966       NA        
28 98         EXACT      TRUE    3528094 10787294        
29 95         FUZZY     FALSE    2603432       NA        
30 99         EXACT     FALSE    5261389       NA        
31 99         EXACT     FALSE    5489996       NA        
32 99         EXACT     FALSE    3425847       NA        
33 99         EXACT     FALSE    2609027       NA        
34 99         EXACT     FALSE    8664645       NA        
35 99         EXACT     FALSE    2610322       NA        
36 98         EXACT      TRUE    2608024 10688503        
37 99         EXACT     FALSE    2599776       NA        
38 98         EXACT      TRUE   11240236  6496469        
39 99         EXACT     FALSE    5260494       NA        
40 99         EXACT     FALSE    2606076       NA        
41 99         EXACT     FALSE    2604141       NA        
   scientificName                                      
1  Acarospora radicata H.Magn.                         
2  Arthonia polymorpha Ach., 1814                      
3  Aspicilia candida (Anzi) Hue                        
4  Aulaxina microphana (Vain.) R.Sant.                 
5  Bacidia kingmanii Hasse                             
6  Buellia griseovirens (Turner & Borrer ex Sm.) Almb. 
7  Calicium quercinum Pers.                            
8  Caloplaca inconspecta Arup                          
9  Catapyrenium caeruleopulvinum J.W.Thomson           
10 Cetraria islandica subsp. islandica                 
11 Cladonia alinii Trass                               
12 Cladonia pleurota (Flörke) Schaer.                  
13 Collema tenax Degel.                                
14 Dirinaria leopoldii (Stein) D.D.Awasthi             
15 Graphis anfractuosa (Eschw.) Eschw.                 
16 Lecanora melaena (Hedl.) Fink                       
17 Lecidea polaris Lynge                               
18 Leptogium austroamericanum (Malme) C.W.Dodge        
19 Nadvornikia hawaiensis (Tuck.) Tibell               
20 Opegrapha cypressi R.C.Harris                       
21 Pannaria conoplea (Ach.) Bory                       
22 Parmelia omphalodes subsp. pinnatifida (Kurok) Skult
23 Peltigera venosa (L.) Hoffm.                        
24 Pertusaria wulfenioides B.de Lesd.                  
25 Phaeographina explicans Fink                        
26 Phylliscum demangeonii (Moug. & Mont.) Nyl.         
27 Placopsis cribellans (Nyl.) Räsänen                 

The only "animal" in this dataset is <i>Triphora minima</i>, which also happens to be an orchid species. To get the correct match, we could re-run the query for this particular species adding the parameter `kingdom = "Plantae"`. You should not do this initially, if you are not 100% sure your data belongs to a certain group. The species labelled as fungi may rather be lichen, as in the case of <i>Usnea</i>, but their classification is plausible, as it is known that the TRY database includes lichens.

Let's check the "HIGHERRANK" matches. ("scientificName" includes authors, "canonicalName" is without authors, and "verbatim_name" is the name queried.)

In [9]:
resP[matchType == "HIGHERRANK", c("scientificName", "canonicalName", "verbatim_name")]


scientificName                         canonicalName       
1   Abies Mill.                            Abies               
2   Acacia Mill.                           Acacia              
3   Acacia Mill.                           Acacia              
4   Aconitum L.                            Aconitum            
5   Adenanthera L.                         Adenanthera         
6   Aesculus L.                            Aesculus            
7   Aloinopsis Schwantes                   Aloinopsis          
8   Alyssum L.                             Alyssum             
9   Ampelocera Klotzsch                    Ampelocera          
10  Asphodeline Rchb.                      Asphodeline         
11  Aucoumea Pierre                        Aucoumea            
12  Poaceae                                Poaceae             
13  Neobartsia Uribe-Convers & Tank        Neobartsia          
14  Beccarianthus Cogn.                    Beccarianthus       
15  Beta maritima L.                       Beta maritima       
16  Betula L.                              Betula              
17  Urticaceae                             Urticaceae          
18  Bromus L.                              Bromus              
19  Calluna vulgaris (L.) Hull             Calluna vulgaris    
20  Campanula stevenii M.Bieb.             Campanula stevenii  
21  Tracheophyta                           Tracheophyta        
22  Carex L.                               Carex               
23  Carex L.                               Carex               
24  Psephellus Cass.                       Psephellus          
25  Asteraceae                             Asteraceae          
26  Chamelaucium Desf.                     Chamelaucium        
27  Dysphania R.Br.                        Dysphania           
28  Chicorium Dumort., 1822                Chicorium           
29  Chrysophyllum L.                       Chrysophyllum       
30  Citrus L.                              Citrus              
⋮   ⋮                                      ⋮                   
138 Scapania paradoxa R.M.Schust.          Scapania paradoxa   
139 Schuurmansia Blume                     Schuurmansia        
140 Scirpus Tourn. ex L.                   Scirpus             
141 Cyperaceae                             Cyperaceae          
142 Scrophularia L.                        Scrophularia        
143 Senna Mill.                            Senna               
144 Sisymbrium L.                          Sisymbrium          
145 Solanum L.                             Solanum             
146 Solanum L.                             Solanum             
147 Fabaceae                               Fabaceae            
148 Sorghum Moench                         Sorghum             
149 Spermacoce L.                          Spermacoce          
150 Sphalmanthus N.E.Br.                   Sphalmanthus        
151 Tabebuia Gomes                         Tabebuia            
152 Asteraceae                             Asteraceae          
153 Taxillus limprichtii (Grüning) H.S.Kiu Taxillus limprichtii
154 Thecanthes Wikstr.                     Thecanthes          
155 Tripleurospermum Sch.Bip.              Tripleurospermum    
156 Ursinia Gaertn.                        Ursinia             
157 Urtica L.                              Urtica              
158 Vallisneria P.Micheli ex L.            Vallisneria         
159 Vangueria Juss.                        Vangueria           
160 Vepris Comm. ex A.Juss.                Vepris              
161 Asteraceae                             Asteraceae          
162 Asteraceae                             Asteraceae          
163 Veronica L.                            Veronica            
164 Vignea P.Beauv.                        Vignea              
165 Viola L.                               Viola               
166 Zollernia Wied-Neuw. & Nees            Zollernia           
167 Zygogynum Baill.                       Zygogynum           
    verbatim_name                   

A large part of the matches are such where the species epithet is given as "sp/sp.", or where authors may be interpreted as parts of the epithets. Preprocessing the names (see name parsing) may help mitigate these issues.



In [10]:
name_backbone("Aconitum napellus")


usageKey scientificName       canonicalName     rank    status   confidence
1 3033665  Aconitum napellus L. Aconitum napellus SPECIES ACCEPTED 97        
  matchType kingdom phylum       order        ⋯ kingdomKey phylumKey classKey
1 EXACT     Plantae Tracheophyta Ranunculales ⋯ 6          7707728   220     
  orderKey familyKey genusKey speciesKey synonym class        
1 399      2410      3033663  3033665    FALSE   Magnoliopsida
  verbatim_name    
1 Aconitum napellus

Let's check the animals now.

In [11]:
table(resA$kingdom)
sum(is.na(resA$kingdom))
table(resA$matchType)



Animalia 
    4821 

[1] 179


     EXACT      FUZZY HIGHERRANK       NONE 
      4408        282        131        179 

Here, classification into animals was unambiguous. Let's check the higher rank matches.

In [12]:
resA[matchType == "HIGHERRANK", c("scientificName", "canonicalName", "verbatim_name")]


scientificName                                                
1   Accipiter Brisson, 1760                                       
2   Achillides chikae                                             
3   Achillides chikae                                             
4   Animalia                                                      
5   Acroporidae                                                   
6   Animalia                                                      
7   Animalia                                                      
8   Acroporidae                                                   
9   Acroporidae                                                   
10  Animalia                                                      
11  Animalia                                                      
12  Strigidae                                                     
13  Anatidae                                                      
14  Trochilidae                                                   
15  Antigone antigone (Linnaeus, 1758)                            
16  Antigone antigone (Linnaeus, 1758)                            
17  Antigone antigone (Linnaeus, 1758)                            
18  Astrapia Vieillot, 1816                                       
19  Australomussa Veron, 1985                                     
20  Brookesia Gray, 1865                                          
21  Brookesia Gray, 1865                                          
22  Buteo Lacepede, 1799                                          
23  Calumma Gray, 1865                                            
24  Candoia Gray, 1842                                            
25  Centrolene Jiménez de la Espada, 1872                         
26  Cerdocyon C.E.H.Smith, 1839                                   
27  Chersobius Fitzinger, 1835                                    
28  Chilabothrus A.M.C.Duméril & Bibron, 1844                     
29  Chilabothrus A.M.C.Duméril & Bibron, 1844                     
30  Antipathidae                                                  
⋮   ⋮                                                             
102 Poritidae                                                     
103 Animalia                                                      
104 Psephotellus Mathews, 1913                                    
105 Pseudastur Mayr, 1998                                         
106 Pseudocordylus Smith, 1838                                    
107 Pseudocordylus Smith, 1838                                    
108 Pseudocordylus Smith, 1838                                    
109 Pyrrhura Bonaparte, 1856                                      
110 Chordata                                                      
111 Sarcoramphus Dumeril, 1805                                    
112 Scaphirhynchus Heckel, 1836                                   
113 Schizoculina Wells, 1937                                      
114 Smaug Stanley, Bauer, Jackman, Branch & Mouton, 2011          
115 Smaug Stanley, Bauer, Jackman, Branch & Mouton, 2011          
116 Smaug Stanley, Bauer, Jackman, Branch & Mouton, 2011          
117 Smaug Stanley, Bauer, Jackman, Branch & Mouton, 2011          
118 Smaug Stanley, Bauer, Jackman, Branch & Mouton, 2011          
119 Smaug Stanley, Bauer, Jackman, Branch & Mouton, 2011          
120 Animalia                                                      
121 Stylaster Gray, 1831                                          
122 Animalia                                                      
123 Animalia                                                      
124 Tapirus Brisson, 1762                                         
125 Toropuku Nielsen, Bauer, Jackman, Hitchmough & Daugherty, 2011
126 Touit G.R.Gray, 1855                                          
127 Trachypithecus Reichenbach, 1862                              
128 Trichoglossus Stephens, 1826                                  
129 Tylototriton Anderson, 1871                    

There are some problems with the classification of specific genera, like <i>Acropora</i>, and there are problems with genera that are erronously repeated within names, like <i>Smaug smaug breyeri</i>. Additionally, family names before the actual scientific names should also be removed. These are issues that can also be alleviated during pre-processing.

### Writing your own name resolution function

Sometimes, you may want to check datasets against a very specific reference database, or your name resolution service of choice may not use the newest version of your reference dataset. In this case, you can write your own name resolution algorithm. Be aware: There are a lot of caveats in this process, and nowadays, it will not be easy to write a function that matches the correctness and efficiency of services like GBIF. Especially when it comes to speed and large datasets, it is unlikely a function that cannot be used in parallel on your own machine or a high performance cluster will deliver results for big datasets within an acceptable time frame.

Let's imagine we want to check our plants dataset against the newest version of the [Leipzig Catalogue of Vascular Plants (LCVP)](https://planthub.idiv.de/LCVP/). 

In [13]:
# read in dataset
LCVP <- fread(paste0(.brd, "PlantHub/LCVP_PlantHub_2024-01-25.gz"))
str(LCVP)


Classes 'data.table' and 'data.frame':	1337778 obs. of  21 variables:
 $ global Id                 : int  1 2 3 4 5 6 7 8 9 10 ...
 $ Input Genus               : chr  "Aa" "Aa" "Aa" "Aa" ...
 $ Input Epitheton           : chr  "argyrolepis" "aurantiaca" "brevis" "calceata" ...
 $ Rank                      : chr  "species" "species" "species" "species" ...
 $ Input Subspecies Epitheton: chr  "" "" "" "" ...
 $ Input Authors             : chr  "(Rchb.f.) Rchb.f." "D.Trujillo" "Schltr." "(Rchb.f.) Schltr." ...
 $ Status                    : chr  "accepted" "accepted" "synonym" "accepted" ...
 $ globalId of Output Taxon  : int  1 2 819078 4 819080 6 7 8 9 10 ...
 $ Output Taxon              : chr  "Aa argyrolepis (Rchb.f.) Rchb.f." "Aa aurantiaca D.Trujillo" "Myrosmodes breve (Schltr.) Garay" "Aa calceata (Rchb.f.) Schltr." ...
 $ family                    : chr  "Orchidaceae" "Orchidaceae" "Orchidaceae" "Orchidaceae" ...
 $ Order                     : chr  "Asparagales" "Asparagales" "Asp

This is an enhanced version of LCVP 2.0, with some errors corrected, and some data added. It includes ASCII-only columns nameIn, authorsIn, nameOut, and authorsOut, as well as links to IPNI, POWO, WFO, and WorldPlants.

Let's set up a simple matching algorithm. You may work on it to include some of the main problematic cases.

First, let's tune our reference list. We would like to be able to identify families and genera before the actual matching, and to do this efficiently, we can extract those from LCVP. We should also be able to directly match complete names with authors, so let's create a column with those, too.

In [14]:
# genera
genera <- sort(unique(sub("\\s.*", "", LCVP$nameIn)))
genera <- genera[genera != ""]
genera[1:10]
# families
families <- sort(unique(LCVP$family))
families <- families[families != ""]
families[1:10]
# name + author column
LCVP[, fullNameIn := trimws(paste(nameIn, authorsIn))]
LCVP$fullNameIn[1:10]


[1] "Aa"          "Aakia"       "Aalius"      "Aaronsohnia" "Abacopteris"
 [6] "Abacosa"     "Abalon"      "Abama"       "Abapus"      "Abarema"

[1] "Acanthaceae"     "Achariaceae"     "Achatocarpaceae" "Acoraceae"      
 [5] "Actinidiaceae"   "Adoxaceae"       "Aextoxicaceae"   "Afrothismiaceae"
 [9] "Agavaceae"       "Agdestidaceae"

[1] "Aa argyrolepis (Rchb.f.) Rchb.f." "Aa aurantiaca D.Trujillo"        
 [3] "Aa brevis Schltr."                "Aa calceata (Rchb.f.) Schltr."   
 [5] "Aa chiogena Schltr."              "Aa colombiana Schltr."           
 [7] "Aa denticulata Schltr."           "Aa erosa (Rchb.f.) Schltr."      
 [9] "Aa fiebrigii (Schltr.) Schltr."   "Aa figueroi Szlach. & S.Nowak"

Let's prepare a results table. For simplicity, we will store the ID of matches in LCVP when a name was found, and indicate whether it is a genus or family found in LCVP (without ID) otherwise.

In [15]:
resTable <- data.table(name = plants$newName, LCVP_ID = numeric(), LCVP_genus = logical(), LCVP_family = logical())


Warning message in as.data.table.list(x, keep.rownames = keep.rownames, check.names = check.names, :
"Item 2 has 0 rows but longest item has 5000; filled with NA"
Warning message in as.data.table.list(x, keep.rownames = keep.rownames, check.names = check.names, :
"Item 3 has 0 rows but longest item has 5000; filled with NA"
Warning message in as.data.table.list(x, keep.rownames = keep.rownames, check.names = check.names, :
"Item 4 has 0 rows but longest item has 5000; filled with NA"


We can ignore the warnings which just tell us that the LCVP columns in the results table are empty for now. Let's fill the table.

In [16]:
# test whether names found in genera
which(plants$newName %in% genera)
# test whether names found in families
which(plants$newName %in% families)

# write data into results
resTable[plants$newName %in% genera, LCVP_genus := TRUE]

resTable[plants$newName %in% families, LCVP_family := TRUE]

# test whether names in nameIn, i.e. names without authors
which(plants$newName %in% LCVP$nameIn)
# test whether names in fullNameIn, i.e. names with authors
which(plants$newName %in% LCVP$fullNameIn)


[1]    5   62  108  517  664 1157 1206 1410 1509 1592 1956 1957 1959 2085 2185
[16] 2290 2452 2660 2692 2864 2892 2904 3125 3639 3679 4029 4452 4642 4703 4930

[1] 1375

[1]    4    6    8    9   12   13   15   16   20   21   25   28   29   30
  [15]   32   33   35   36   39   41   42   52   53   54   56   57   58   59
  [29]   60   61   65   68   71   72   73   75   79   80   81   82   84   89
  [43]   90   91   92   93   94   95   96   98   99  100  102  105  106  107
  [57]  109  110  111  112  113  114  115  116  119  120  123  124  126  127
  [71]  130  131  135  136  137  139  142  143  144  148  149  150  151  152
  [85]  154  157  160  161  162  163  164  165  166  167  168  170  171  173
  [99]  179  180  181  182  184  188  190  192  193  194  195  196  197  198
 [113]  199  202  205  207  211  212  213  214  217  218  220  221  224  227
 [127]  228  229  230  231  232  233  234  235  237  238  239  243  246  249
 [141]  250  252  253  254  255  258  260  262  263  264  265  267  268  270
 [155]  271  274  276  277  282  283  284  285  286  287  289  290  293  295
 [169]  297  299  300  301  302  304  305  306  307  308  309  310  312  313
 [183]  314  316  317  319  320  322  323  324  325  326  328  329  330  331
 [197]  332  334  337  338  339  340  341  343  344  348  350  351  352  355
 [211]  361  362  363  364  366  367  368  369  371  374  376  377  379  380
 [225]  381  383  385  386  387  388  389  390  392  393  394  395  396  397
 [239]  398  400  401  402  403  404  405  407  409  411  413  414  415  417
 [253]  418  421  423  425  426  428  429  430  431  433  435  437  441  442
 [267]  446  447  448  450  452  453  454  457  460  461  462  463  464  465
 [281]  467  470  471  473  474  477  478  479  480  481  482  484  486  489
 [295]  490  491  493  494  497  498  500  504  505  508  509  510  511  512
 [309]  514  515  516  518  521  522  523  524  525  526  529  530  531  534
 [323]  538  542  544  548  549  550  551  552  553  554  555  557  559  560
 [337]  562  566  567  568  570  573  574  576  579  581  583  588  589  590
 [351]  591  594  595  596  597  598  599  600  602  603  604  605  606  607
 [365]  608  611  612  614  616  617  619  620  622  624  625  626  627  629
 [379]  630  631  633  636  637  638  639  641  642  643  644  645  646  647
 [393]  648  650  651  652  654  655  658  663  665  666  667  668  669  670
 [407]  674  675  678  679  680  681  683  685  686  687  688  696  698  701
 [421]  702  703  705  707  708  710  714  715  718  719  720  721  722  723
 [435]  724  726  727  728  729  730  731  732  733  734  735  736  737  738
 [449]  742  743  747  748  749  750  751  752  753  755  756  759  761  762
 [463]  763  765  766  767  768  769  770  771  772  773  774  776  777  778
 [477]  779  780  781  782  783  784  785  786  787  788  790  791  792  793
 [491]  794  795  801  802  803  806  807  808  810  813  815  817  821  822
 [505]  828  829  831  832  833  834  835  837  838  839  840  842  843  844
 [519]  846  848  849  850  851  852  853  854  856  858  860  862  863  865
 [533]  866  867  871  873  874  875  876  877  878  883  887  888  889  891
 [547]  892  894  895  896  897  898  902  905  906  907  909  910  911  912
 [561]  913  919  921  924  925  928  931  932  933  934  935  936  937  938
 [575]  939  941  942  943  944  949  950  951  954  956  957  958  960  961
 [589]  962  963  964  965  966  967  968  969  970  972  973  976  978  979
 [603]  983  984  987  988  991  993  994  995  996  997 1001 1004 1005 1006
 [617] 1007 1012 1013 1014 1015 1017 1020 1021 1023 1025 1027 1029 1030 1031
 [631] 1034 1035 1036 1037 1038 1040 1041 1043 1044 1046 1047 1048 1049 1050
 [645] 1051 1053 1054 1055 1056 1057 1058 1060 1061 1063 1064 1065 1067 1070
 [659] 1072 1074 1077 1080 1082 1084 1085 1088 1091 1092 1094 1095 1096 1097
 [673] 1098 1101 1102 1104 1105 1106 1107 1108 1109 1110 1111 1112 1116 1117
 [687] 1121 1122 1123 1124 1125 1126 1127 1128 1129 1130 1132 1133 1135 1136
 [701] 1137 1138 1139 1140 1141 1142 1143 1144 1145 1147 1148 1150 1154 1155
 [715] 1156 1158 1160 1161 1162 1163 1164 1165 1166 1168 1169 1171 1172 1173

[1]   14   17   18   24   27   40   55   78   83   86   97  101  104  117  118
 [16]  121  122  129  132  147  156  176  178  183  185  186  200  201  203  206
 [31]  208  215  216  219  222  241  248  251  257  272  278  291  294  296  298
 [46]  303  336  342  345  347  349  358  360  372  384  434  436  438  439  440
 [61]  451  456  458  459  469  475  483  487  488  501  502  535  537  561  571
 [76]  572  575  577  578  580  582  584  585  586  587  592  593  601  610  621
 [91]  632  653  657  672  673  682  689  694  706  713  716  717  725  740  741
[106]  744  745  746  757  760  775  796  800  809  841  845  847  855  868  881
[121]  884  893  899  903  908  915  918  922  927  930  948  952  953  955  974
[136]  980  990  992  998 1000 1009 1010 1011 1016 1018 1019 1028 1032 1033 1042
[151] 1045 1062 1066 1068 1071 1073 1079 1099 1114 1119 1134 1167 1175 1181 1187
[166] 1188 1193 1195 1196 1197 1198 1222 1223 1229 1239 1243 1255 1265 1273 1278
[181] 1285 1286 1287 1289 1290 1292 1295 1297 1298 1299 1300 1301 1306 1308 1328
[196] 1332 1338 1339 1346 1360 1361 1364 1366 1369 1376 1406 1433 1439 1442 1444
[211] 1449 1452 1485 1488 1491 1499 1500 1519 1523 1524 1527 1545 1567 1568 1573
[226] 1587 1600 1601 1605 1611 1623 1629 1637 1642 1644 1651 1652 1661 1680 1681
[241] 1692 1716 1719 1729 1756 1759 1763 1764 1767 1777 1778 1784 1788 1797 1808
[256] 1810 1836 1843 1850 1851 1853 1862 1874 1875 1876 1882 1897 1899 1903 1904
[271] 1906 1907 1908 1912 1914 1917 1918 1919 1921 1922 1926 1927 1928 1930 1933
[286] 1936 1937 1940 1948 1955 1958 1962 1980 1984 1988 1989 1993 1997 2000 2004
[301] 2006 2010 2021 2023 2024 2028 2045 2048 2050 2055 2058 2060 2064 2066 2068
[316] 2069 2070 2071 2078 2080 2088 2094 2098 2107 2110 2138 2141 2145 2158 2168
[331] 2170 2172 2184 2210 2211 2221 2230 2232 2237 2246 2249 2254 2256 2272 2273
[346] 2276 2277 2320 2328 2345 2347 2360 2363 2368 2375 2387 2393 2395 2400 2401
[361] 2414 2416 2419 2430 2437 2443 2444 2482 2487 2492 2495 2496 2498 2502 2511
[376] 2519 2527 2535 2541 2554 2559 2572 2575 2594 2596 2610 2622 2629 2635 2680
[391] 2690 2703 2716 2725 2733 2746 2770 2793 2813 2820 2823 2833 2834 2836 2837
[406] 2852 2874 2875 2879 2885 2886 2899 2909 2919 2925 2950 2952 2960 2963 2964
[421] 2965 2966 2968 2978 2985 2998 3001 3002 3011 3026 3050 3056 3061 3073 3092
[436] 3119 3121 3124 3142 3151 3158 3159 3169 3170 3171 3172 3173 3182 3214 3227
[451] 3232 3234 3236 3238 3241 3259 3274 3284 3298 3301 3304 3305 3314 3315 3321
[466] 3330 3346 3347 3349 3366 3367 3369 3386 3413 3416 3419 3420 3426 3434 3435
[481] 3441 3446 3452 3456 3461 3469 3493 3495 3497 3509 3511 3512 3518 3536 3545
[496] 3546 3550 3559 3572 3577 3583 3586 3589 3593 3599 3604 3606 3607 3608 3611
[511] 3612 3614 3615 3616 3626 3631 3634 3652 3664 3665 3676 3704 3706 3714 3720
[526] 3726 3732 3734 3736 3737 3739 3740 3749 3752 3778 3786 3788 3792 3794 3817
[541] 3834 3848 3856 3879 3885 3891 3903 3921 3922 3938 3948 3949 3956 3966 3973
[556] 3979 3985 3991 4002 4020 4051 4069 4070 4089 4102 4106 4137 4141 4146 4148
[571] 4154 4164 4166 4203 4207 4220 4242 4252 4257 4269 4274 4278 4283 4304 4307
[586] 4311 4317 4319 4321 4322 4329 4332 4339 4340 4342 4346 4347 4353 4355 4367
[601] 4369 4383 4388 4389 4393 4394 4396 4398 4402 4404 4408 4409 4416 4449 4456
[616] 4458 4461 4492 4503 4509 4512 4515 4521 4527 4528 4532 4535 4544 4548 4549
[631] 4555 4560 4583 4601 4605 4606 4623 4639 4658 4659 4676 4691 4692 4700 4701
[646] 4709 4730 4741 4743 4748 4754 4755 4758 4765 4769 4794 4819 4836 4839 4840
[661] 4853 4857 4859 4860 4861 4864 4868 4878 4882 4886 4890 4895 4901 4905 4911
[676] 4914 4936 4945 4947 4951 4960 4962 4968 4987 4990 4998 4999

As we can see, there are many matches both when searching with and without authors. However, for names without authors, there may be more than one name in the reference list (they are called homonyms). Only one of those will be an accepted name, while the others are synonyms. As the matched names without authors do not allow for a disambiguation, we will assign the ID of the accepted name from the reference list, if there are several. To do this, we create a copy of the reference list, order by taxonomic status so that accepted names come first, and only keep the first of several rows with identical names without authors. We then use this reduced list to extract the respective IDs.

In [17]:
# create a copy of the reference list
LCVPUnique <- LCVP
# order by taxonomic status
setorder(LCVPUnique, status)
# keep only the first of several rows with identical names without authors
LCVPUnique <- unique(LCVPUnique, by = "nameIn")

# check whether it worked
nrow(LCVPUnique)
nrow(LCVP)


[1] 1256502

[1] 1337778

We removed about 80000 names from LCVP in this process. Let's now get the IDs.

In [18]:
# write data into results, extract LCVP ID
setkey(LCVP, fullNameIn)
res <- LCVP[plants$newName]
resTable[is.na(LCVP_ID), LCVP_ID := res$`global Id`[is.na(resTable$LCVP_ID)]]

setkey(LCVPUnique, nameIn)
res <- LCVPUnique[plants$newName]
resTable[is.na(LCVP_ID), LCVP_ID := res$`global Id`[is.na(resTable$LCVP_ID)]]


We can now check what remains from the names in our list. The remainder will be the difficult part where the algorihm used actually matters. 

In [19]:
plants[, matched := FALSE]
plants[!is.na(resTable$LCVP_ID) | !is.na(resTable$LCVP_genus) | !is.na(resTable$LCVP_family), matched := TRUE]
table(plants$matched)



FALSE  TRUE 
 1180  3820 

From the 5000 names we had to check, 1180 remain to be tested. This is a relatively large number, as this dataset is especially messy, but good for us to practice. We should have a look at the unmatched names.

In [20]:
plants[matched == FALSE]$newName[1:20]


[1] ""                                                            
 [2] "(lauraceae) pubescente"                                      
 [3] "?Betulaceae sp."                                             
 [4] "Abies sp"                                                    
 [5] "Abuta_panamensis"                                            
 [6] "Abutilon grandiflorum G.Don Orthodox"                        
 [7] "Acacia contriva"                                             
 [8] "Acacia eremophila W.Fitzg. var. variabilis Maiden & Blakeley"
 [9] "Acacia flavescens A.Cunn. ex Benth. Orthodox?"               
[10] "Acacia incanicarpa A.R.Chapman & Maslin"                     
[11] "Acacia mucronata Willd. ex H.L.Wendl. subsp. mucronata"      
[12] "Acacia plectocarpa A.Cunn. ex Benth. Orthodox"               
[13] "Acacia sclerosperma F.Muell. subsp. sclerosperma"            
[14] "Acacia sp1887"                                               
[15] "Acacia auriculiformis A.Cunn. ex Benth."                     
[16] "Acacia colei Maslin & L.A.J.Thomson"                         
[17] "Acacia drummondii Lindl."                                    
[18] "Acacia hadrophylla R.S.Cowan & Maslin"                       
[19] "Acacia lazaridis Pedley"                                     
[20] "Acacia neriifolia A.Cunn. ex Benth."

It seems that in the first place, we should get rid of author names, as there spelling may be different from the one in LCVP and therefore not produce a match. A very simple way of doing so would be to cut names after the second whitespace.

In [21]:
# function to extract first two words
nameShorter <- function(x) {
	# get number of whitespaces
	ws <- gregexpr(" ", x)
	# get position of second whitespace if available, otherweise return 0
	ws <- sapply(ws, function(x) if (length(x) > 1) x[2] else 0)
	x[ws > 0] <- substr(x[ws > 0], 1, ws[ws > 0] - 1)
	return(x)
}
print(nameShorter(plants$newName[40:50]))


 [1] "Acacia tortilis"                  "Acacia valida"                   
 [3] "Acacia yorkrakinensis"            "Acacia auriculiformis A.Cunn. ex"
 [5] "Acacia colei Maslin &"            "Acacia drummondii Lindl."        
 [7] "Acacia hadrophylla R.S.Cowan &"   "Acacia lazaridis Pedley"         
 [9] "Acacia neriifolia A.Cunn. ex"     "Acacia ptychoclada Maiden &"     
[11] "Acacia speckii R.S.Cowan &"      


We see that some of the shortNames are not as expected. Thare are still author names linked to them. The reason is that there are protected whitespaces in there. We need to remove them first.

In [22]:
# function to extract first two words
nameShorter <- function(x) {
	# remove protected whitespaces
	x <- gsub("\xc2\xa0", " ", x)
	# get number of whitespaces
	ws <- gregexpr(" ", x)
	# get position of second whitespace if available, otherweise return 0
	ws <- sapply(ws, function(x) if (length(x) > 1) x[2] else 0)
	x[ws > 0] <- substr(x[ws > 0], 1, ws[ws > 0] - 1)
	return(x)
}
print(nameShorter(plants$newName[40:50]))


 [1] "Acacia tortilis"       "Acacia valida"         "Acacia yorkrakinensis"
 [4] "Acacia auriculiformis" "Acacia colei"          "Acacia drummondii"    
 [7] "Acacia hadrophylla"    "Acacia lazaridis"      "Acacia neriifolia"    
[10] "Acacia ptychoclada"    "Acacia speckii"       


This looks much nicer. We can now do the name matching without authors again. Note that, ideally, we would not just match without authors, but also measure the difference between author names so that we actually select the closest match.

In [23]:
plants[, shortName := nameShorter(newName)]

setkey(LCVPUnique, nameIn)
res <- LCVPUnique[plants$shortName]
resTable[is.na(LCVP_ID), LCVP_ID := res$`global Id`[is.na(resTable$LCVP_ID)]]

# update the "notMatched" column
plants[!is.na(resTable$LCVP_ID) | !is.na(resTable$LCVP_genus) | !is.na(resTable$LCVP_family), matched := TRUE]
table(plants$matched)



FALSE  TRUE 
  581  4419 

As we can see, the number of unmatched names was reduced from 1211 to 581. We could now introduce some fuzzy matching, i.e. try to assign names from the reference list to names with spelling errors. Of course we could also consider other pre-processing options: correcting the uppercase/lowercase of the names, removing special characters like question marks or underlines, removing "sp.", etc.. 

In [24]:
plants[matched == FALSE]$shortName[1:50]


[1] ""                             "(lauraceae) pubescente"      
 [3] "?Betulaceae sp."              "Abies sp"                    
 [5] "Abuta_panamensis"             "Acacia contriva"             
 [7] "Acacia sp1887"                "Acarospora radicata"         
 [9] "Acer sino-oblongum"           "Aconitum delphiniifolium"    
[11] "Adenanthera sp."              "A-Elyhordeum schaackianum"   
[13] "Aeranthus muscicola"          "Aesculus xworlitzensis"      
[15] "Agathis mooeri"               "Agave vera-cruz"             
[17] "Agrosthophyllum bicuspidatum" "Albizia NA"                  
[19] "Alectryon macrococcus"        "Alexa wachenheimii"          
[21] "Alissum tortuosum"            "Allium scabrifolium"         
[23] "Aloinopsis gydouwensis"       "ALOPECURUS GENICULATUS,"     
[25] "Alstroemeria riedeliana"      "Alyssum caliacre"            
[27] "Alyssum thunbergii"           "Amaroria soulameiodes"       
[29] "Ampelocera indet"             "Amphibromus NA"              
[31] "Anartia meyeri"               "Ancistrocladus stelliger"    
[33] "Andopogon glomeratus"         "ANEMONE NEMOROSA"            
[35] "Anona squamosa"               "Anthaenantia villosa"        
[37] "Anthocephalus sp."            "Anthurium lezamai"           
[39] "Aquilegia coerulea"           "Arctoa hyperborea"           
[41] "Arctostaphylos_obispoensis"   "Ardisia brevipetala"         
[43] "Aristida sanctae-luciae"      "Arrabidaea trailii"          
[45] "Artemisia "                   "Arthonia polymorpha"         
[47] "Artocarpus lessigiana"        "Arundinella khaseana"        
[49] "Asperula rechingeri"          "Asphodeline fistulosus"

The fuzzy matching will be done in a loop using a matching function. Later on, this will allow us to easily switch to parallel processing. The below function first checks for the presence of the first word, assumed to be the genus, in the reference list. If it is found, the fuzzy matching will only be done on the species belonging to this genus, massively reducing the computation time. Then, fuzzy matching is done, the best result(s) selected and the first of the best results or no result returned (in case there is none).

In [25]:
# create a template to return in case there is no match
resTemplate <- LCVPUnique[1]
resTemplate[1] <- NA

# function for fuzzy matching
# maxDist controls the Levenshtein distance, i.e. the difference between the given and matched name
nameMatcher <- function(x, maxDist = 2) {
	genus <- sub("\\s.*", "", x$shortName)
	if (genus %in% genera) {
		checkRows <- sub("\\s.*", "", LCVPUnique$nameIn) == genus
	} else {
		checkRows <- rep(TRUE, nrow(LCVPUnique))
	}
	# do fuzzy matching
	res <- LCVPUnique[checkRows][agrepl(paste0("^", x$shortName, "$"), LCVPUnique$nameIn[checkRows],
		max.distance = maxDist, fixed = FALSE
	)]
	if (nrow(res) > 0) {
		# calculate Levenshtein distance
		dists <- adist(x$shortName, res$nameIn)
		# keep best result(s)
		res <- res[as.vector(dists == min(dists))]
		# return first result or return template
		return(res[1])
	} else {
		return(resTemplate)
	}
}


Let's run this function on some of the remaining unmatched names. As this may take a while, we will only loop over the first 200 names. You may run it on the whole dataset, but expect it to take about half an hour. Running on the first 200 names will just take a minute.

In [26]:
timeStart <- Sys.time()
# for (i in seq_len(nrow(plants))) {
for (i in seq_len(200)) {
	# only check unmatched cases
	if (plants$matched[i] == FALSE) {
		# counter to show progress
		print(paste(i, Sys.time()))
		res <- nameMatcher(plants[i])
		if (!is.na(res$`global Id`)) {
			resTable[i, LCVP_ID := res$`global Id`]
			plants[i, matched := TRUE]
		}
	}
}
Sys.time() - timeStart


[1] "1 2024-04-12 11:58:24.400659"
[1] "2 2024-04-12 11:58:28.823094"
[1] "3 2024-04-12 11:58:34.227135"
[1] "7 2024-04-12 11:58:37.908572"
[1] "10 2024-04-12 11:58:38.654882"
[1] "19 2024-04-12 11:58:42.660404"
[1] "38 2024-04-12 11:58:43.418891"
[1] "63 2024-04-12 11:58:44.179911"
[1] "70 2024-04-12 11:58:48.752534"
[1] "87 2024-04-12 11:58:49.515793"
[1] "103 2024-04-12 11:58:50.269285"
[1] "125 2024-04-12 11:58:51.013671"
[1] "128 2024-04-12 11:58:56.107607"
[1] "133 2024-04-12 11:59:00.12651"
[1] "141 2024-04-12 11:59:00.888705"
[1] "146 2024-04-12 11:59:01.645952"
[1] "158 2024-04-12 11:59:02.720926"
[1] "174 2024-04-12 11:59:07.297597"
[1] "187 2024-04-12 11:59:08.048403"
[1] "189 2024-04-12 11:59:08.804925"
[1] "191 2024-04-12 11:59:09.561838"


Time difference of 49.24616 secs

In [27]:
plants[c(1, 10, 19, 128, 133)]


oldName                newName                matched shortName             
1                                               FALSE                         
2 Abuta_panamensis       Abuta_panamensis        TRUE   Abuta_panamensis      
3 Acacia contriva        Acacia contriva        FALSE   Acacia contriva       
4 Aeranthus muscicola    Aeranthus muscicola     TRUE   Aeranthus muscicola   
5 Aesculus xworlitzensis Aesculus xworlitzensis  TRUE   Aesculus xworlitzensis

What we see from the times needed per individual run is that whenever the genus is found, matching is relatively fast, taking about a second, but when this is not the case, it is quite slow. This is because agrepl() then works on the whole LCVPUnique dataset and has to compare more than one million pairs of words. You could think about a heuristic to reduce the number of rows checked.

### Parallel processing

We will now focus on speeding up the process of name checking by running it in parallel. Let's check how many cores are available on the system.

In [28]:
parallel::detectCores()


[1] 16

On my machine, I can at maximum use 16 cores. That means that I can expect a more or less 16-fold increase in processing time. Assuming that the matching of all unmatched names of the 5000 row dataset would take 30 minutes when running it sequentially, that means that I can expect the task to be completed in about 2 minutes when running in parallel. However, there comes a cost with it: When running processes in parallel, R will copy all the objects in the workspace needed for each parallel process, and in our cases, that means copying LCVPUnique 16 times. This will take quite some time, and for few iterations of the loop, initializing the parallel process will take more time than is saved by running in parallel. Anyway, we will first try the first 200 names we already processed before (but note that the matched ones will not be done again, because they are matched).

We also need to make some adjustments to the code. As the parallel processes will use their copies of the data, it would not make sense to let them write to the individual copies. Therefore, if a match is found, the information needs to be returned to the main process. Also, as objects are copied for individual workers, the information needed for the individual processes should be kept minimal. I will also not make use of all available cores to make sure I can do others stuff on my computer without delay while the process is running.

In [29]:
# create the cluster for parallel processing
cl <- makeCluster(parallel::detectCores() - 1)
registerDoSNOW(cl)

# run the name resolution in parallel
timeStart <- Sys.time()
resTemp <- foreach(i = seq_len(200), .combine = c, .packages = c("data.table")) %dopar% {
	# only check unmatched cases
	# return the global Id if it is found and NA if not checked or nothing could be found
	if (plants$matched[i] == FALSE) {
		res <- nameMatcher(plants[i])
		res <- res$`global Id`
	} else {
		res <- NA
	}
	# indicate what to return
	res
}
Sys.time() - timeStart
# stop the cluster
stopCluster(cl)


Time difference of 3.274923 mins

The process took about 3.5 mins for me with 15 cores, so no gain in terms of time for now. Let's see what we got.

In [30]:
resTemp


[1] NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA
 [26] NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA
 [51] NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA
 [76] NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA
[101] NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA
[126] NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA
[151] NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA
[176] NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA NA

As we already ran the process sequentially, new matches were not to be expected on the first 200 entries. Let's risk running the process on the whole dataset.

In [31]:
# create the cluster for parallel processing
cl <- makeCluster(parallel::detectCores() - 1)
registerDoSNOW(cl)

# run the name resolution in parallel
timeStart <- Sys.time()
resTemp <- foreach(i = seq_len(nrow(plants)), .combine = c, .packages = c("data.table")) %dopar% {
	# only check unmatched cases
	# return the global Id if it is found and NA if not checked or nothing could be found
	if (plants$matched[i] == FALSE) {
		res <- nameMatcher(plants[i])
		res <- res$`global Id`
	} else {
		res <- NA
	}
	# indicate what to return
	res
}
Sys.time() - timeStart

# stop the cluster
stopCluster(cl)


Time difference of 7.922978 mins

This took about 7.5 mins. That's a big improvement compared to the sequential process. Let's see how many matches we got.

In [32]:
table(!is.na(resTemp))



FALSE  TRUE 
 4749   251 

So out of the 581 names, another 251 could be matched. Let's transfer the data into resTable. It might well be worth thinking about adding information on type of matching, as the fuzzy matches are not perfect any might require further checking. However, our current implementation does not give us any information on the type of match.

In [33]:
resTable[!is.na(resTemp), LCVP_ID := resTemp[!is.na(resTemp)]]
plants[!is.na(resTable$LCVP_ID), matched := TRUE]


Let's just look at the results and the remaining names. Maybe you can figure out some possible improvements to the code.

>TASKS:
>1) For example, you could think about allowing for partial matches, if the genus is found, but not the species. This could easily be implemented by extracting the first word from the shortName column.
>2) You could also play with the `maxDist` parameter to increase or decrease the Levenshtein distance. 
>3) To improve the speed of the `nameMatcher` function, you would certainly have to filter potential matches, for example by only including names starting with a certain letter (assuming the first letter is correct), or by only including names with a certain number of characters. 
>4) Finally, the code would be more efficient if you would only loop over the rows that have not been matched yet.

In [34]:
table(plants$matched)
plants[matched == FALSE][1:20]



FALSE  TRUE 
  319  4681 

oldName                               newName                              
1                                                                             
2  (lauraceae) pubescente                (lauraceae) pubescente               
3  ?Betulaceae sp.                       ?Betulaceae sp.                      
4  Abies sp                              Abies sp                             
5  Acacia contriva                       Acacia contriva                      
6  Acacia sp1887                         Acacia sp1887                        
7  Acarospora radicata                   Acarospora radicata                  
8  Adenanthera sp.                       Adenanthera sp.                      
9  A-Elyhordeum schaackianum             A-Elyhordeum schaackianum            
10 Albizia NA                            Albizia NA                           
11 Allium scabrifolium                   Allium scabrifolium                  
12 Aloinopsis gydouwensis                Aloinopsis gydouwensis               
13 ALOPECURUS GENICULATUS,               ALOPECURUS GENICULATUS,              
14 Alyssum thunbergii Moq. Orthodox p    Alyssum thunbergii Moq. Orthodox p   
15 Ampelocera indet                      Ampelocera indet                     
16 Amphibromus NA                        Amphibromus NA                       
17 Ancistrocladus stelliger Wall. ex DC. Ancistrocladus stelliger Wall. ex DC.
18 ANEMONE NEMOROSA L.                   ANEMONE NEMOROSA L.                  
19 Anthocephalus sp.                     Anthocephalus sp.                    
20 Arctoa hyperborea                     Arctoa hyperborea                    
   matched shortName                
1  FALSE                            
2  FALSE   (lauraceae) pubescente   
3  FALSE   ?Betulaceae sp.          
4  FALSE   Abies sp                 
5  FALSE   Acacia contriva          
6  FALSE   Acacia sp1887            
7  FALSE   Acarospora radicata      
8  FALSE   Adenanthera sp.          
9  FALSE   A-Elyhordeum schaackianum
10 FALSE   Albizia NA               
11 FALSE   Allium scabrifolium      
12 FALSE   Aloinopsis gydouwensis   
13 FALSE   ALOPECURUS GENICULATUS,  
14 FALSE   Alyssum thunbergii       
15 FALSE   Ampelocera indet         
16 FALSE   Amphibromus NA           
17 FALSE   Ancistrocladus stelliger 
18 FALSE   ANEMONE NEMOROSA         
19 FALSE   Anthocephalus sp.        
20 FALSE   Arctoa hyperborea